# Multivariate Adaptive Regression Splines (MARS)

### Step 1 - Import libraries

In [3]:
# Main libraries
import pandas as pd # for data manipulation
import numpy as np # for data manipulation
from sklearn.linear_model import LinearRegression # for building a linear regression model
from pyearth import Earth # for building a mars model
import plotly.graph_objects as go # for data visualization
import plotly.express as px # for data visualization

### Step 2 - Get the data for our model (from Kaggle)

or this analysis, we will use Kaggle house price data which you can download from here https://www.kaggle.com/quantbruce/real-estate-price-prediction?select=Real+estate.csv

After downloading it, we read csv into a Pandas dataframe

In [6]:
df = pd.read_csv('Real estate.csv', encoding='utf-8')
df

No  X1 transaction date  X2 house age  \
0      1             2012.917          32.0   
1      2             2012.917          19.5   
2      3             2013.583          13.3   
3      4             2013.500          13.3   
4      5             2012.833           5.0   
..   ...                  ...           ...   
409  410             2013.000          13.7   
410  411             2012.667           5.6   
411  412             2013.250          18.8   
412  413             2013.000           8.1   
413  414             2013.500           6.5   

     X3 distance to the nearest MRT station  X4 number of convenience stores  \
0                                  84.87882                               10   
1                                 306.59470                                9   
2                                 561.98450                                5   
3                                 561.98450                                5   
4                                 390.56840                                5   
..                                      ...                              ...   
409                              4082.01500                                0   
410                                90.45606                                9   
411                               390.96960                                7   
412                               104.81010                                5   
413                                90.45606                                9   

     X5 latitude  X6 longitude  Y house price of unit area  
0       24.98298     121.54024                        37.9  
1       24.98034     121.53951                        42.2  
2       24.98746     121.54391                        47.3  
3       24.98746     121.54391                        54.8  
4       24.97937     121.54245                        43.1  
..           ...           ...                         ...  
409     24.94155     121.50381                        15.4  
410     24.97433     121.54310                        50.0  
411     24.97923     121.53986                        40.6  
412     24.96674     121.54067                        52.5  
413     24.97433     121.54310                        63.9  

[414 rows x 8 columns]

### Step 3 - Linear Regression vs. MARS (1 independent variable)

Let's create a scatter plot showing the distance from nearest MRT station (independent variable) and house price per unit area (dependent a.k.a. target variable)

In [7]:
# Create a scatter plot
fig = px.scatter(df, x=df['X3 distance to the nearest MRT station'], y=df['Y house price of unit area'], 
                 opacity=0.8, color_discrete_sequence=['black'])

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'))

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black')

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black')

# Set figure title
fig.update_layout(title_text="Scatter Plot")

# Update marker size
fig.update_traces(marker=dict(size=3))

fig.show()

##### Train MARS and Linear Regression models

You can igonre numpy warning

In [14]:
# --- Select variables to use in the two models --- 
# Note, we need X to be a 2D array, hence reshape
X=df['X3 distance to the nearest MRT station'].values.reshape(-1,1)
y=df['Y house price of unit area'].values

# To silence Numpy future warning
np.linalg.lstsq.rcond=-1

# --- Define and fit the two models ---
model1 = LinearRegression() 
model2 = Earth(max_terms=500, max_degree=1) # note, terms in brackets are the hyperparameters 

LR = model1.fit(X, y)
MARS = model2.fit(X, y)

# --- Print model summary ---
# LR
print("Simple Linear Regression Model")
print("--------------------------------------")
print("Intercept: ", LR.intercept_)
print("Slope: ", LR.coef_)

print("")
print("<><><><><><><><><><><><><><><><><><><>")
print("")

# MARS
print(MARS.summary())

Simple Linear Regression Model
--------------------------------------
Intercept:  45.85142705777498
Slope:  [-0.00726205]

<><><><><><><><><><><><><><><><><><><>

Earth Model
-------------------------------------
Basis Function  Pruned  Coefficient  
-------------------------------------
(Intercept)     No      31.4145      
h(x0-1146.33)   Yes     None         
h(1146.33-x0)   No      0.0184597    
x0              No      -0.00269698  
-------------------------------------
MSE: 79.1935, GCV: 81.5398, RSQ: 0.5712, GRSQ: 0.5606


/Users/solclover/opt/anaconda3/envs/saulenv36/lib/python3.6/site-packages/pyearth/earth.py:802: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.

/Users/solclover/opt/anaconda3/envs/saulenv36/lib/python3.6/site-packages/pyearth/earth.py:1055: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.



##### Plot MARS and Linear Regression on a graph

In [16]:
# ----- Create data for Linear Regression line -----
# Create 20 evenly spaced points from smallest X to largest X
x_range = np.linspace(X.min(), X.max(), 20) 

# Predict y values for our set of X values
y_range = model1.predict(x_range.reshape(-1, 1))



# ----- Create data for MARS model line -----
# Select a few points including the 3 major ones: min, max and hinge
x_mars = np.array([X.min(), 1000, 1146.33, 2000, 3000, 4000, 5000, 6000, X.max()])

# Predict y values for our set of X values
y_mars = model2.predict(x_mars.reshape(-1, 1))



# ----- Create a scatter plot -----
fig = px.scatter(df, x=df['X3 distance to the nearest MRT station'], y=df['Y house price of unit area'], 
                 opacity=0.8, color_discrete_sequence=['black'])

# Add a best-fit line
fig.add_traces(go.Scatter(x=x_range, y=y_range, name='Linear Regression', line=dict(color='limegreen')))
fig.add_traces(go.Scatter(x=x_mars, y=y_mars, name='MARS', line=dict(color='red')))

# Change chart background color
fig.update_layout(dict(plot_bgcolor = 'white'))

# Update axes lines
fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black')

fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey', 
                 zeroline=True, zerolinewidth=1, zerolinecolor='lightgrey', 
                 showline=True, linewidth=1, linecolor='black')

# Set figure title
fig.update_layout(title_text="Linear Regression vs. MARS")

# Update marker size
fig.update_traces(marker=dict(size=3))

fig.show()

### Step 4 - Linear Regression vs. MARS (2 independent variables)

First, let's create a 3D scatter plot containing distance from MRT and house age (our two independent variables) and house price per unit area (our dependent a.k.a target variable)

In [17]:
# Create a 3D scatter plot
fig = px.scatter_3d(df, x=df['X3 distance to the nearest MRT station'], y=df['X2 house age'], z=df['Y house price of unit area'], 
                 opacity=0.8, color_discrete_sequence=['black'])

# Set figure title
fig.update_layout(title_text="Scatter 3D Plot",
                  scene = dict(xaxis=dict(backgroundcolor='white',
                                          color='black',
                                          gridcolor='lightgrey'),
                               yaxis=dict(backgroundcolor='white',
                                          color='black',
                                          gridcolor='lightgrey'
                                          ),
                               zaxis=dict(backgroundcolor='white',
                                          color='black', 
                                          gridcolor='lightgrey')))

# Update marker size
fig.update_traces(marker=dict(size=3))

fig.show()

# Export chart to HTML file
#fig.write_html('Scatter_3D.html')

##### Fit MARS and Linear Regression models

You can ignore numpy warning

In [19]:
# ----- Select variables that we want to use in a model -----
# Note, X in this case is already a 2D array, hence no reshape
X=df[['X3 distance to the nearest MRT station','X2 house age']]
y=df['Y house price of unit area'].values

# ----- Define and fit the two models -----
model1 = LinearRegression()
model2 = Earth()

LR = model1.fit(X, y)
MARS = model2.fit(X, y)

# ----- Print model summary -----
# LR
print("Simple Linear Regression Model")
print("--------------------------------------")
print("Intercept: ", LR.intercept_)
print("Slope: ", LR.coef_)

print("")
print("<><><><><><><><><><><><><><><><><><><>")
print("")

# MARS
print(MARS.summary())

Simple Linear Regression Model
--------------------------------------
Intercept:  49.885585756906636
Slope:  [-0.00720862 -0.23102658]

<><><><><><><><><><><><><><><><><><><>

Earth Model
------------------------------------------------------------------------
Basis Function                                     Pruned  Coefficient  
------------------------------------------------------------------------
(Intercept)                                        No      23.0218      
h(X3 distance to the nearest MRT station-1146.33)  No      -0.00246985  
h(1146.33-X3 distance to the nearest MRT station)  No      0.0196908    
h(X2 house age-27.6)                               No      0.482925     
h(27.6-X2 house age)                               No      0.446568     
X3 distance to the nearest MRT station             Yes     None         
------------------------------------------------------------------------
MSE: 69.3776, GCV: 73.2167, RSQ: 0.6244, GRSQ: 0.6055


/Users/solclover/opt/anaconda3/envs/saulenv36/lib/python3.6/site-packages/pyearth/earth.py:802: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.

/Users/solclover/opt/anaconda3/envs/saulenv36/lib/python3.6/site-packages/pyearth/earth.py:1055: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.



Select our independent and dependent variables

In [228]:
X=df[['X3 distance to the nearest MRT station','X2 house age']]
y=df['Y house price of unit area'].values

Define and fit the two models

In [229]:
model1 = LinearRegression()
model2 = pyearth.Earth()

LR = model1.fit(X, y)
MARS = model2.fit(X, y)

/Users/solclover/opt/anaconda3/envs/saulenv36/lib/python3.6/site-packages/pyearth/earth.py:802: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.

/Users/solclover/opt/anaconda3/envs/saulenv36/lib/python3.6/site-packages/pyearth/earth.py:1055: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.



##### Prepare mesh before drawing predictions on a 3D graph 

In [20]:
# Increments between points in a meshgrid
mesh_size = 5

# Identify min and max values for input variables
x_min, x_max = X['X3 distance to the nearest MRT station'].min(), X['X3 distance to the nearest MRT station'].max()
y_min, y_max = X['X2 house age'].min(), X['X2 house age'].max()

# Return evenly spaced values based on a range between min and max
xrange = np.arange(x_min, x_max, mesh_size)
yrange = np.arange(y_min, y_max, mesh_size)

# Create a meshgrid
xx, yy = np.meshgrid(xrange, yrange)

# Predict using LR model
pred_LR = model1.predict(np.c_[xx.ravel(), yy.ravel()])
pred_LR = pred_LR.reshape(xx.shape)

# Predict using MARS model
pred_MARS = model2.predict(np.c_[xx.ravel(), yy.ravel()])
pred_MARS = pred_MARS.reshape(xx.shape)

# Note, .ravel() flattens the array to a 1D array,
# then np.c_ takes elements from flattened xx and yy arrays and puts them together,
# this creates the right shape required for model input

# prediction array that is created by the model output is a 1D array,
# we need to reshape it to be the same shape as xx or yy to be able to display it on a graph

##### Draw 3D predictions graph for Linear Regression

In [21]:
# Create a 3D scatter plot with predictions
fig = px.scatter_3d(df, x=df['X3 distance to the nearest MRT station'], y=df['X2 house age'], z=df['Y house price of unit area'], 
                 opacity=0.8, color_discrete_sequence=['black'])

# Set figure title and colors
fig.update_layout(title_text="Scatter 3D Plot with Linear Regression Prediction Surface",
                  scene = dict(xaxis=dict(backgroundcolor='white',
                                          color='black',
                                          gridcolor='lightgrey'),
                               yaxis=dict(backgroundcolor='white',
                                          color='black',
                                          gridcolor='lightgrey'
                                          ),
                               zaxis=dict(backgroundcolor='white',
                                          color='black', 
                                          gridcolor='lightgrey')))
# Update marker size
fig.update_traces(marker=dict(size=3))

# Add prediction plane
fig.add_traces(go.Surface(x=xrange, y=yrange, z=pred_LR, name='LR'))

fig.show()

##### Draw 3D predictions graph for MARS

In [22]:
# Create a 3D scatter plot with predictions
fig = px.scatter_3d(df, x=df['X3 distance to the nearest MRT station'], y=df['X2 house age'], z=df['Y house price of unit area'], 
                 opacity=0.8, color_discrete_sequence=['black'])

# Set figure title and colors
fig.update_layout(title_text="Scatter 3D Plot with MARS Prediction Surface",
                  scene = dict(xaxis=dict(backgroundcolor='white',
                                          color='black',
                                          gridcolor='lightgrey'),
                               yaxis=dict(backgroundcolor='white',
                                          color='black',
                                          gridcolor='lightgrey'
                                          ),
                               zaxis=dict(backgroundcolor='white',
                                          color='black', 
                                          gridcolor='lightgrey')))
# Update marker size
fig.update_traces(marker=dict(size=3))

# Add prediction plane
fig.add_traces(go.Surface(x=xrange, y=yrange, z=pred_MARS, name='MARS', ))
                          #colorscale=px.colors.sequential.Viridis))

fig.show()

# End of Program